In [1]:
import pandas as pd
import numpy as np

In [19]:
from IPython.display import display, HTML
display(HTML("<style>.container { width:100% !important; }</style>"))
pd.set_option('display.max_rows', 50000)
pd.set_option('display.max_columns', 50000)
pd.set_option('display.width', 100000)


In [10]:
#import plotly.go
import matplotlib.pyplot as plt
import plotly.graph_objects as go
from plotly.subplots import make_subplots


In [4]:
data_0 = pd.read_csv(r'C:\Users\ayush\Desktop\IITB\IMCP_2\round-3-island-data-bottle\prices_round_3_day_0.csv', sep=';')
data_1 = pd.read_csv(r'C:\Users\ayush\Desktop\IITB\IMCP_2\round-3-island-data-bottle\prices_round_3_day_1.csv', sep=';')
data_2 = pd.read_csv(r'C:\Users\ayush\Desktop\IITB\IMCP_2\round-3-island-data-bottle\prices_round_3_day_2.csv', sep=';')


In [5]:
data_0.head()

day  timestamp       product  bid_price_1  bid_volume_1  bid_price_2  \
0    0          0     CHOCOLATE         7999           111          NaN   
1    0          0  STRAWBERRIES         3999           210          NaN   
2    0          0         ROSES        14999            72          NaN   
3    0          0   GIFT_BASKET        71348            19      71347.0   
4    0        100   GIFT_BASKET        71344             1      71343.0   

   bid_volume_2  bid_price_3  bid_volume_3  ask_price_1  ask_volume_1  \
0           NaN          NaN           NaN         8001           111   
1           NaN          NaN           NaN         4001           210   
2           NaN          NaN           NaN        15001            72   
3          24.0          NaN           NaN        71362            19   
4          12.0      71342.0          20.0        71355             1   

   ask_price_2  ask_volume_2  ask_price_3  ask_volume_3  mid_price  \
0          NaN           NaN          NaN           NaN     8000.0   
1          NaN           NaN          NaN           NaN     4000.0   
2          NaN           NaN          NaN           NaN    15000.0   
3      71363.0          24.0          NaN           NaN    71355.0   
4      71356.0          12.0      71357.0          20.0    71349.5   

   profit_and_loss  
0              0.0  
1              0.0  
2              0.0  
3              0.0  
4              0.0

In [6]:
## plot using plotly
data = pd.concat([data_0, data_1, data_2], axis=0)

data['timestamp'] += data['day'] * 1e6

In [ ]:
plot_data(data, [''])

In [21]:
data_choco = data[data['product'] == 'CHOCOLATE']
data_straw = data[data['product'] == 'STRAWBERRIES']
data_rose = data[data['product'] == 'ROSES']
data_gift = data[data['product'] == 'GIFT_BASKET']

In [34]:
def add_spread(data):
    data['spread'] = data['ask_price_1'] - data['bid_price_1']
    data.reset_index(drop=True, inplace=True)
add_spread(data_choco)
add_spread(data_straw)
add_spread(data_rose)
add_spread(data_gift)

C:\Users\ayush\AppData\Local\Temp\ipykernel_25760\2770141709.py:2: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

C:\Users\ayush\AppData\Local\Temp\ipykernel_25760\2770141709.py:2: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

C:\Users\ayush\AppData\Local\Temp\ipykernel_25760\2770141709.py:2: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/panda

In [36]:
data_gift['spread'].describe()

count    30000.000000
mean        10.864000
std          2.377062
min          1.000000
25%         11.000000
50%         11.000000
75%         13.000000
max         14.000000
Name: spread, dtype: float64

In [42]:
data_gift['valuation'] = 4 * data_choco['mid_price'] + 6 * data_straw['mid_price'] + data_rose['mid_price'] 

C:\Users\ayush\AppData\Local\Temp\ipykernel_25760\1385181905.py:1: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [43]:
data_gift['diff'] = data_gift['valuation'] - data_gift['mid_price']

C:\Users\ayush\AppData\Local\Temp\ipykernel_25760\1506370250.py:1: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [52]:
data_gift['diff'].describe()

count    30000.000000
mean      -379.490483
std         76.424382
min       -632.000000
25%       -430.000000
50%       -381.000000
75%       -329.000000
max       -140.000000
Name: diff, dtype: float64

## Helper functions


In [59]:
def calculate_macd(df, fast_period=3, slow_period=99, signal_period=2):
    # Calculate the short-term exponential moving average (EMA)
    ema_fast = df['mid_price'].ewm(span=fast_period).mean()
    
    # Calculate the long-term exponential moving average (EMA)
    ema_slow = df['mid_price'].ewm(span=slow_period).mean()
    
    # Calculate the MACD line
    macd_line = ema_fast - ema_slow
    
    # Calculate the signal line
    signal_line = macd_line.ewm(span=signal_period).mean()
    
    # Calculate the MACD histogram
    macd_hist = macd_line - signal_line
    
    df['macd_line'] = macd_line
    df['signal_line'] = signal_line
    df['macd_hist'] = macd_hist

    return df

In [58]:
def plot_sunlight_humidity_orchids(data):
    fig = go.Figure()

    # Add SUNLIGHT trace
    fig.add_trace(go.Scatter(x=data['timestamp'], y=data['bid_price_1'], name='bid_price_1'))

    # Add HUMIDITY trace
    fig.add_trace(go.Scatter(x=data['timestamp'], y=data['bid_price_2'], name='bid_price_2'))

    # Add ORCHIDS trace
    fig.add_trace(go.Scatter(x=data['timestamp'], y=data['ask_price_1'], name='ask_price_1'))

    # Add export target trace   
    fig.add_trace(go.Scatter(x=data['timestamp'], y=data['ask_price_2'], name='ask_price_2'))

    # fig.add_trace(go.Scatter(x=data['timestamp'], y=data['IMPORT_TARIFF'], name='IMPORT_TARIFF', yaxis='y5'))

    # Update layout
    fig.update_layout(title='Sunlight, Humidity, and Orchids',
                    xaxis_title='Timestamp',
                    yaxis=dict(title='SUNLIGHT', side='left'))
                    

    # Show the plot
    fig.show()

plot_sunlight_humidity_orchids(data_straw)

In [77]:
plot_sunlight_humidity_orchids(data_rose)

In [53]:
def print_corrs(df, alphas, rets = ['ret_10', 'ret_30', 'ret_1', 'ret_5']):
# def print_corrs(df, alphas, rets = ['ret_10', 'ret_30', 'iv_10']):
# def print_corrs(df, alphas, rets = ['tick_10', 'tick_30', 'tick_60', 'tick_300']):
# def print_corrs(df, alphas, rets = ['ret_60', 'ret_300', 'iv_60']):
    msg = "                                      "
    for ret in rets:
        msg += f"{ret:>8s}"
    print(msg)
    for alpha in alphas:
        msg = f"{alpha:30s} corr -> "
        for ret in rets:
            msg += f"{df[alpha].corr(df[ret])*100:7.2f} "
        print(msg)
    print()

In [54]:
def print_buckets(df, alphas, rets = ['ret_10', 'ret_5', 'ret_30', 'ret_300'], aggfunc = ['mean', 'median', 'count'], buckets = 5):
# def print_buckets(df, alphas, rets = ['ret_10', 'ret_30', 'iv_10'], aggfunc = ['mean', 'median', 'count']):
# def print_buckets(df, alphas, rets = ['tick_10', 'tick_30', 'tick_60', 'tick_300'], aggfunc = ['mean', 'median', 'count']):
# def print_buckets(df, alphas, rets = ['ret_60', 'ret_300', 'iv_60'], aggfunc = ['mean', 'median', 'count']):
    for alpha in alphas:
        msg = df.pivot_table(index = pd.qcut(df[alpha],buckets,duplicates='drop'), values=rets, aggfunc=aggfunc)
        print(msg)

In [69]:
def add_ret(df, periods = [1, 5, 10, 30, 60, 300]):
    for period in periods:
        df[f'ret_{period}'] = df['mid_price'].pct_change(period).shift(-period) * 1e4
    return df
df = add_ret(data_gift)
_ = add_ret(data_choco)
_ = add_ret(data_straw)
_ = add_ret(data_rose)

C:\Users\ayush\AppData\Local\Temp\ipykernel_25760\212480902.py:3: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

C:\Users\ayush\AppData\Local\Temp\ipykernel_25760\212480902.py:3: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

C:\Users\ayush\AppData\Local\Temp\ipykernel_25760\212480902.py:3: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-d

In [56]:
print_corrs(df, ['mid_price', 'spread', 'diff'])
print_buckets(df, ['mid_price', 'spread', 'diff'])

                                        ret_10  ret_30   ret_1   ret_5
mid_price                      corr ->   -1.05   -1.61   -0.35   -0.74 
spread                         corr ->    1.01    0.54    0.28    0.20 
diff                           corr ->   10.27   17.21    3.45    7.41 

                          mean                                  median                                count                     
                        ret_10    ret_30   ret_300     ret_5    ret_10    ret_30   ret_300     ret_5 ret_10 ret_30 ret_300 ret_5
mid_price                                                                                                                       
(69344.499, 69917.0]  0.037331  0.026607 -0.160144  0.019826  0.071555  0.071916 -2.576324  0.000000   5996   5976    5706  6001
(69917.0, 70801.5]   -0.177676 -0.455079 -6.117996 -0.085565 -0.214440 -0.428532 -5.390644 -0.141534   6009   6009    6009  6009
(70801.5, 71022.5]    0.069822  0.137267  3.933176  0.034673  0.070

## Analysing plots

In [76]:
data_choco['diff'] = data_gift['diff']
data_straw['diff'] = data_gift['diff']
data_rose['diff'] = data_gift['diff']

print_corrs(data_choco, ['diff'])
print_corrs(data_straw, ['diff'])
print_corrs(data_rose, ['diff'])


print_buckets(data_choco, ['diff'])
print_buckets(data_straw, ['diff'])
print_buckets(data_rose, ['diff'])

C:\Users\ayush\AppData\Local\Temp\ipykernel_25760\1508075795.py:1: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

C:\Users\ayush\AppData\Local\Temp\ipykernel_25760\1508075795.py:2: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

C:\Users\ayush\AppData\Local\Temp\ipykernel_25760\1508075795.py:3: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/panda

                                        ret_10  ret_30   ret_1   ret_5
diff                           corr ->    2.06    3.40    0.57    1.50 

                                        ret_10  ret_30   ret_1   ret_5
diff                           corr ->    3.24    5.93    0.34    1.92 

                                        ret_10  ret_30   ret_1   ret_5
diff                           corr ->   -0.27   -0.74   -0.21   -0.17 

                        mean                               median                            count                     
                      ret_10    ret_30   ret_300     ret_5 ret_10    ret_30   ret_300 ret_5 ret_10 ret_30 ret_300 ret_5
diff                                                                                                                   
(-632.001, -442.5] -0.175482 -0.589101 -5.368009 -0.105686    0.0 -0.641272 -6.327312   0.0   6006   6006    5998  6006
(-442.5, -399.5]   -0.130146 -0.185269 -0.940991 -0.052463    0.0  0.000000 -1.251251   

## MACD params on each of the indivisual elements

In [65]:
def calculate_max_corr(df):
    max_corr = 1
    max_period = ()
    for fast_period in range(24, 50):
        for slow_period in range(40, 80):
            for signal_period in range(20, 40):
                df_macd = calculate_macd(df, fast_period, slow_period, signal_period)
                corr = df_macd['macd_hist'].corr(df_macd['ret_10'])
                if corr < max_corr:
                    max_corr = corr
                    max_period = (fast_period, slow_period, signal_period)
    return max_corr, max_period

In [70]:
calculate_max_corr(data_straw)

C:\Users\ayush\AppData\Local\Temp\ipykernel_25760\553696339.py:17: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

C:\Users\ayush\AppData\Local\Temp\ipykernel_25760\553696339.py:18: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

C:\Users\ayush\AppData\Local\Temp\ipykernel_25760\553696339.py:19: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/panda

(-0.004015210164896296, (41, 40, 25))

In [67]:
# data_choco/.head()

day  timestamp    product  bid_price_1  bid_volume_1  bid_price_2  bid_volume_2  bid_price_3  bid_volume_3  ask_price_1  ask_volume_1  ask_price_2  ask_volume_2  ask_price_3  ask_volume_3  mid_price  profit_and_loss  spread     ret_1     ret_5    ret_10    ret_30    ret_60    ret_300  macd_line  signal_line  macd_hist
0    0        0.0  CHOCOLATE         7999           111          NaN           NaN          NaN           NaN         8001           111          NaN           NaN          NaN           NaN     8000.0              0.0       2  1.875000  1.875000  3.125000  3.125000 -4.375000  45.000000   0.000000     0.000000   0.000000
1    0      100.0  CHOCOLATE         8001            52       8000.0          95.0          NaN           NaN         8002           147          NaN           NaN          NaN           NaN     8001.5              0.0       1 -0.624883  0.624883  0.000000  1.249766 -4.999063  43.741798   0.005812     0.002981   0.002832
2    0      200.0  CHOCOLATE         8000           152          NaN           NaN          NaN           NaN         8002           152          NaN           NaN          NaN           NaN     8001.0              0.0       2  1.874766  3.124609 -3.124609  3.749531 -4.999375  44.369454   0.005051     0.003707   0.001345
3    0      300.0  CHOCOLATE         8002            44       8001.0          84.0          NaN           NaN         8003           128          NaN           NaN          NaN           NaN     8002.5              0.0       1 -0.624805  0.000000 -2.499219  2.499219 -6.872852  44.361137   0.013556     0.006362   0.007194
4    0      400.0  CHOCOLATE         8001           118          NaN           NaN          NaN           NaN         8003           118          NaN           NaN          NaN           NaN     8002.0              0.0       2 -0.624844  0.624844 -2.499375  1.874531 -6.248438  43.114221   0.015277     0.008332   0.006945